In [2]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from tab_transformer_pytorch import TabTransformer, FTTransformer
from preprocessing import get_features_and_target
from sklearn.preprocessing import LabelEncoder
from RMSELoss import RMSELoss
import plotly.graph_objects as go

# Getting Dataframe

In [3]:
train_df = pd.read_csv("data/train_data.csv")
dev_df = pd.read_csv("data/development_data.csv")

target_column = "PullTest (N)"  

x_train, y_train = get_features_and_target(train_df, target_column)
x_dev, y_dev = get_features_and_target(dev_df, target_column)



# Encode Categorical_Features

In [4]:
# Define the categorical features
categorical_features = ["Material"]

le = LabelEncoder()

for feature in categorical_features:
    x_train[feature] = le.fit_transform(x_train[feature])
    x_dev[feature] = le.transform(x_dev[feature])  

# Split Categorical_Features

In [5]:
# Drop categorical features to get the continuous features
x_train_numerical_features = x_train.drop(categorical_features, axis=1)
x_dev_numerical_features = x_dev.drop(categorical_features, axis=1)

# Seperate the categorical features
x_train_categorical_features = x_train[categorical_features]
x_dev_categorical_features = x_dev[categorical_features]

# Change df into Tensors

In [6]:
train_tensor = torch.tensor(x_train.to_numpy(), dtype=torch.float)
x_train_numer_tensor = torch.tensor(x_train_numerical_features.to_numpy(),dtype=torch.float)
x_dev_numer_tensor = torch.tensor(x_dev_numerical_features.to_numpy(),dtype=torch.float)
y_train_tensor = torch.tensor(y_train.to_numpy(), dtype=torch.float)

dev_tensor = torch.tensor(x_dev.to_numpy(), dtype=torch.float)
x_train_categorical_features_tensor = torch.tensor(x_train_categorical_features.to_numpy(),dtype=torch.long)
x_dev_categorical_features_tensor = torch.tensor(x_dev_categorical_features.to_numpy(),dtype=torch.long)
y_dev_tensor = torch.tensor(y_dev.to_numpy(), dtype=torch.float)

from torch.utils.data import TensorDataset,DataLoader

train_ds = TensorDataset(
    x_train_categorical_features_tensor,
    x_train_numer_tensor,
    y_train_tensor
)
val_ds = TensorDataset(
    x_dev_categorical_features_tensor,
    x_dev_numer_tensor,
    y_dev_tensor
)
g = torch.Generator()
g.manual_seed(42)
train_loader = DataLoader(train_ds, batch_size=32, shuffle=True, generator= g)
val_loader   = DataLoader(val_ds,   batch_size=32)



# Check Tensors


In [6]:
#torch.set_printoptions(sci_mode=False, precision=3)
#print(x_train_numer_tensor)

# Define Model

In [7]:
# categories is defined as a tuple, we only have one categorical feature "Material"
# the second parameter has to be empty for the model to work correctly
# in hard numbers this is displaying (1,)
model = FTTransformer(
    categories=(x_train_categorical_features.shape[1],),
    num_continuous=x_train_numerical_features.shape[1],
    dim=8,
    dim_out=1,
    depth=4,
    heads=4,
    attn_dropout=0.1,
    ff_dropout=0.1
)

# Physical Epoch


In [8]:
# Make sure these indices match the *positions* of your “Thickness A (mm)” 
# and “Thickness B (mm)” in the x_cont tensor!
# If you built x_cont from a DataFrame like:
#    cont_cols = ["Thickness A (mm)", "Thickness B (mm)", …]
# then idxA = 0, idxB = 1
idxA, idxB = 5, 6  

def physics_pull_force(x_cont):
    # x_cont: [B, num_cont_features]
    A = x_cont[:, idxA]               # shape [B]
    B = x_cont[:, idxB]               # shape [B]

    # element‐wise minimum of each row
    # torch.minimum was added in PyTorch 1.7+
    t = torch.minimum(A, B)           # shape [B]
    # now compute f_phys = (π/4)*(5*√t)^2*(0.6*365)
    # keep it as [B] so we can later unsqueeze to [B,1]
    return ((torch.pi / 4) * (4 * torch.sqrt(t)).pow(2) * (0.8 * 365))


def train_one_epoch(train_loader):
    total_error     = 0.0


    for x_cat, x_cont, y in train_loader:
        optimizer.zero_grad()

        # ensure y is [B,1]
        y = y.unsqueeze(-1)
    # [B,1]



        # physics target (no grads needed for f_phys)
        with torch.no_grad():
            f_phys = physics_pull_force(x_cont).unsqueeze(-1)    # [B]
            
        # MSE to the physics‐based target
        True_Error = y - f_phys

        # forward
        pred = model(x_cat, x_cont)   

        # loss
        error_res_loss = criterion(pred, True_Error)

        # combined loss
        loss = error_res_loss
        loss.backward()
        optimizer.step()

        total_error += loss.item()



    return total_error / len(train_loader)




# Physical Training

In [16]:
from datetime import datetime

criterion = RMSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.0001)

#Changeable Parameters
# ----------------------------------------------------#
#Model description for saving
model_description    = 'lr0.0001_8_1_4_4_.1_.1Error'

# Number of epochs to train
EPOCHS = 30000

# Hyperparam to weight the physics loss
lambda_phys = 4
#-----------------------------------------------------#

# Lists to store per‐epoch losses
train_data_losses       = []
val_data_losses         = []


best_vloss   = float('inf')
last_ckpt  = None
timestamp    = datetime.now().strftime('%Y%m%d')



for epoch in range(EPOCHS):
    print(f'\nEPOCH {epoch+1}/{EPOCHS}')

    # --------------------
    # 1) TRAINING PHASE
    # --------------------
    model.train()
    train_data = train_one_epoch(train_loader)

    train_data_losses.append(train_data)
    print(f'train loss: {train_data:.4f}')

    # --------------------
    # 2) VALIDATION PHASE
    # --------------------
    model.eval()
    
    val_loss = 0.0
    with torch.no_grad():
        for x_cat, x_cont, y in val_loader:
            y = y.unsqueeze(-1)
            pred = model(x_cat, x_cont)



            A = x_cont[:, idxA]
            B = x_cont[:, idxB]
            t = torch.minimum(A, B)
            f_phys = physics_pull_force(x_cont)    # [B]
            f_phys = f_phys.unsqueeze(-1) 


            True_Error = y - f_phys

            # 1) loss
            val_loss += criterion(pred, True_Error).item()

    avg_vloss = val_loss / len(val_loader)


    val_data_losses.append(avg_vloss)


    print(f'valid loss: {avg_vloss:.4f}')
    

    # --------------------
    # 3) CHECKPOINTING
    # --------------------
    if (epoch + 1) % 100 == 0 and avg_vloss < best_vloss:
        if last_ckpt is not None:
            os.remove(last_ckpt)

        best_vloss = avg_vloss
        ckpt_path = f'trained_models/physical_error_training/model_{model_description}_date_{timestamp}_epoch{epoch+1}.pt'
        torch.save(model.state_dict(), ckpt_path)
        last_ckpt = ckpt_path



EPOCH 1/30000
train loss: 339.5516
valid loss: 354.8405

EPOCH 2/30000
train loss: 344.1191
valid loss: 355.2655

EPOCH 3/30000
train loss: 348.6225
valid loss: 355.2937

EPOCH 4/30000
train loss: 334.5628
valid loss: 351.6071

EPOCH 5/30000
train loss: 344.0707
valid loss: 335.8342

EPOCH 6/30000
train loss: 338.8886
valid loss: 334.9256

EPOCH 7/30000
train loss: 354.7955
valid loss: 334.8373

EPOCH 8/30000
train loss: 343.4646
valid loss: 334.7557

EPOCH 9/30000
train loss: 332.2279
valid loss: 334.7078

EPOCH 10/30000
train loss: 363.8090
valid loss: 334.6590

EPOCH 11/30000
train loss: 353.7703
valid loss: 334.6128

EPOCH 12/30000
train loss: 343.8651
valid loss: 334.7595

EPOCH 13/30000
train loss: 342.9081
valid loss: 334.7686

EPOCH 14/30000
train loss: 359.2488
valid loss: 334.6923

EPOCH 15/30000
train loss: 352.2752
valid loss: 334.4453

EPOCH 16/30000
train loss: 328.7167
valid loss: 334.5387

EPOCH 17/30000
train loss: 344.1162
valid loss: 335.0234

EPOCH 18/30000
train l

In [17]:
from sklearn.metrics import r2_score


r2 = r2_score(y, pred)
print(f"R² = {r2:.4f}")

R² = -291.5662


Only Physics Lambda 1:

train loss: 121.9670
valid loss: 148.8158

In [18]:
import plotly.graph_objects as go

fig = go.Figure()

# Training loss trace
fig.add_trace(go.Scatter(
    y=train_data_losses,
    mode="lines+markers",
    name="Train Data Loss",
    line=dict(color="lightblue", width=2),
    marker=dict(size=4)
))

# Validation loss trace
fig.add_trace(go.Scatter(
    y=val_data_losses,
    mode="lines+markers",
    name="Validation Data Loss",
    line=dict(color="orange", width=2),
    marker=dict(size=4)
))

# Layout
fig.update_layout(
    title="Training & Validation Loss over Epochs  - lr0.00025_8_1_4_4_.3_.3 - Physics Lambda 4",
    xaxis_title="Epoch",
    yaxis_title="Loss",
    xaxis=dict(
        tickmode='array',
        tickvals=list(range(0, 10500, 500)),  # Show ticks every 100 epochs
        tickfont=dict(size=10)
    ),
    template="plotly_white",
    legend=dict(
        x=0.7,        # push legend past the right edge
        y=1,
        xanchor="left",
        borderwidth=1
    ),
    margin=dict(t=60, b=40)  # give extra room on right for the legend
)

fig.show()


In [22]:
import plotly.graph_objects as go

epochs = list(range(1, len(train_data_losses) + 1))

fig = go.Figure()

# Training loss trace
fig.add_trace(go.Scatter(
    x=epochs,
    y=train_data_losses,
    mode="lines",
    name="Train Data Loss",
    line=dict(color="lightblue", width=2)
))

fig.add_trace(go.Scatter(
    x=epochs,
    y=train_phys_losses,
    mode="lines",
    name="Train Physical Loss",
    line=dict(color="royalblue", width=2)
))

fig.add_trace(go.Scatter(
    x=epochs,
    y=train_dataphys_losses,
    mode="lines",
    name="Train Data+Physical Loss",
    line=dict(color="black", width=2)
))

# Validation loss trace
fig.add_trace(go.Scatter(
    x=epochs,
    y=val_data_losses,
    mode="lines",
    name="Validation Data Loss",
    line=dict(color="orange", width=2, dash="dash")
))

fig.add_trace(go.Scatter(
    x=epochs,
    y=val_phys_losses,
    mode="lines",
    name="Validation Physical Loss",
    line=dict(color="tomato", width=2, dash="dash")
))

fig.add_trace(go.Scatter(
    x=epochs,
    y=val_dataphys_losses,
    mode="lines",
    name="Validation Data+Physical Loss",
    line=dict(color="firebrick", width=2, dash="dash")
))

# Layout enhancements
fig.update_layout(
    title="Training & Validation Loss over 10 000 Epochs - lr0.00025_8_1_4_4_.3_.3 - Physics Lambda 4",
    xaxis_title="Epoch",
    yaxis_title="Loss",
    xaxis=dict(
        tickmode='array',
        tickvals=list(range(0, 10500, 500)),  # Show ticks every 100 epochs
        tickfont=dict(size=10)
    ),
    yaxis=dict(
        tickformat=".2e" if max(train_data_losses + val_data_losses) > 1e4 else ".4f",  # Dynamic formatting
        gridcolor="lightgray"
    ),
    legend=dict(
        x=0.7,        # push legend past the right edge
        y=1,
        xanchor="left",
        borderwidth=1
    ),
    
    template="plotly_white",
    margin=dict(t=60, b=40)
)

fig.show()


In [ ]:
import numpy as np
from sklearn.metrics import mean_absolute_error, mean_squared_error

# Collect predictions and true values from the validation set
model.eval()
all_preds = []
all_targets = []

with torch.no_grad():
    for x_categ, x_numer, y_train in val_loader:
        preds = model(x_categ, x_numer).squeeze().cpu().numpy()
        all_preds.extend(preds)
        all_targets.extend(y_train.cpu().numpy())

all_preds = np.array(all_preds)
all_targets = np.array(all_targets)

# Inverse-transform predictions and targets to original units
preds_orig = y_train
targets_orig = y_train

# Calculate MAE and RMSE in original units
mae = mean_absolute_error(targets_orig, preds_orig)
rmse = np.sqrt(mean_squared_error(targets_orig, preds_orig))

print(f"MAE (original units): {mae:.2f}")
print(f"RMSE (original units): {rmse:.2f}")

MAE (original units): 0.00
RMSE (original units): 0.00
